In [1]:
from espnet_model_zoo.downloader import ModelDownloader

d = ModelDownloader()
cfg = d.download_and_unpack("espnet/Wangyou_Zhang_chime4_enh_train_enh_conv_tasnet_raw")

Fetching 16 files:  19%|█▉        | 3/16 [00:02<00:08,  1.52it/s]Error while downloading from https://cdn-lfs.hf.co/repos/7d/11/7d1189f017ae8546bf3f5b69dc2c32c4ea3aacf8fa6812028b9436ae1771125d/afedfa8ff65bf256b02e390301ee75ba67dc5d7d1f83f48a76aa2b9610c44c86?response-content-disposition=inline%3B+filename*%3DUTF-8%27%275epoch.pth%3B+filename%3D%225epoch.pth%22%3B&Expires=1730623465&Policy=eyJTdGF0ZW1lbnQiOlt7IkNvbmRpdGlvbiI6eyJEYXRlTGVzc1RoYW4iOnsiQVdTOkVwb2NoVGltZSI6MTczMDYyMzQ2NX19LCJSZXNvdXJjZSI6Imh0dHBzOi8vY2RuLWxmcy5oZi5jby9yZXBvcy83ZC8xMS83ZDExODlmMDE3YWU4NTQ2YmYzZjViNjlkYzJjMzJjNGVhM2FhY2Y4ZmE2ODEyMDI4Yjk0MzZhZTE3NzExMjVkL2FmZWRmYThmZjY1YmYyNTZiMDJlMzkwMzAxZWU3NWJhNjdkYzVkN2QxZjgzZjQ4YTc2YWEyYjk2MTBjNDRjODY%7EcmVzcG9uc2UtY29udGVudC1kaXNwb3NpdGlvbj0qIn1dfQ__&Signature=p-ks46-GDBKcvYsOyxTLtgQN9sAJ-h5EH8q8CPlQsNSctsdnMIP%7EzwZGZ601Sp3fbItb%7EdZ5Xpx4e5teCRLLdCsLk0ckiscwlSXvkb8%7E3iIscEMxZuUV-C9HyFfP%7EnhvH3HfYoK5HWA-dMWeCmPmAu42lQ3s6emAl6VuS4p%7EgjfC7QkbVvzNk3RUgZPGW2HlrjwQLw9hDU0OiM

In [11]:
import sys
import soundfile
from espnet2.bin.enh_inference import SeparateSpeech


separate_speech = {}
# For models downloaded from GoogleDrive, you can use the following script:
enh_model_sc = SeparateSpeech(
  train_config=cfg["train_config"],
  model_file=cfg["model_file"],
  # for segment-wise process on long speech
  normalize_segment_scale=False,
  show_progressbar=True,
  ref_channel=4,
  normalize_output_wav=True,
  device="cuda:0",
)

Eps is deprecated in si_snr loss, set clamp_db instead.


In [ ]:
import soundfile
from IPython.display import display, Audio
mixwav_mc, sr = soundfile.read("C:/Users/Liudong/Desktop/MyData/对话.wav")
# mixwav.shape: num_samples, num_channels
mixwav_sc = mixwav_mc[:,1]
display(Audio(mixwav_mc.T, rate=sr))

In [9]:
print(mixwav_sc.shape)

(519057,)


In [12]:
wave = enh_model_sc(mixwav_sc[None, ...], sr)
print("Input real noisy speech", flush=True)
display(Audio(mixwav_mc.T, rate=sr))
print("Enhanced speech", flush=True)
display(Audio(wave[0].squeeze(), rate=sr))

Input real noisy speech


Enhanced speech


### 上面是提取语音的部分，测试效果比较差，原因可能是因为噪声音频是合成的，和真实情况下的噪声音频具有差别
### 实验证明，上面的猜想是错的!!!

In [2]:
fs = 8000 #@param {type:"integer"}
tag = "lichenda/wsj0_2mix_skim_noncausal"

In [3]:
import sys
import soundfile
from espnet_model_zoo.downloader import ModelDownloader
from espnet2.bin.enh_inference import SeparateSpeech

d = ModelDownloader()

cfg = d.download_and_unpack(tag)
separate_speech = SeparateSpeech(
  train_config=cfg["train_config"],
  model_file=cfg["model_file"],
  # for segment-wise process on long speech
  segment_size=2.4,
  hop_size=0.8,
  normalize_segment_scale=False,
  show_progressbar=True,
  ref_channel=None,
  normalize_output_wav=True,
  device="cuda:0",
)

Fetching 16 files: 100%|██████████| 16/16 [00:16<00:00,  1.01s/it]


Eps is deprecated in si_snr loss, set clamp_db instead.


In [6]:
import os
import soundfile
from IPython.display import display, Audio

mixwav, sr = soundfile.read("C:/Users/Liudong/Desktop/MyData/mixed_audio_with_length_of_b2_simple.wav")
waves_wsj = separate_speech(mixwav[None, ...], fs=sr)

print("Input mixture", flush=True)
display(Audio(mixwav, rate=sr))
print(f"========= Separated speech with model {tag} =========", flush=True)
print("Separated spk1", flush=True)
display(Audio(waves_wsj[0].squeeze(), rate=sr))
print("Separated spk2", flush=True)
display(Audio(waves_wsj[1].squeeze(), rate=sr))

100%|██████████| 7/7 [00:06<00:00,  1.08it/s]

Input mixture


========= Separated speech with model lichenda/wsj0_2mix_skim_noncausal =========
Separated spk1


Separated spk2
